In [53]:
# Importing data paths
import sys
sys.path.insert(1, '/Users/piyush/Desktop/dsml_Portfolio/podcast/final_push')
from config import PODCASTS_DATABASE_PATH_RAW, USER_REVIEWS_DATABASE_PATH_RAW, PODCASTS_DATABASE_PATH_PROCESSED, USER_REVIEWS_DATABASE_PATH_PROCESSED
import pandas as pd
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.metrics.pairwise import cosine_similarity, manhattan_distances, euclidean_distances
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split
import re
from gensim import models
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.style
import seaborn as sns
import plotly.express as px
import plotly.figure_factory as ff
%matplotlib inline
from gensim.models import FastText as ft
from IPython.display import Image

In [54]:
import nltk
import ssl

try:
    _create_unverified_https_context = ssl._create_unverified_context
except AttributeError:
    pass
else:
    ssl._create_default_https_context = _create_unverified_https_context

nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')
nltk.download('omw-1.4')

[nltk_data] Downloading package punkt to /Users/piyush/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/piyush/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /Users/piyush/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package omw-1.4 to /Users/piyush/nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!


True

In [55]:
PODCASTS_DATABASE_PATH_RAW, USER_REVIEWS_DATABASE_PATH_RAW

('/Users/piyush/Desktop/dsml_Portfolio/podcast/final_push/data/raw/podcasts.csv',
 '/Users/piyush/Desktop/dsml_Portfolio/podcast/final_push/data/raw/user_reviews.csv')

In [117]:
# Loading data 
df_podcasts = pd.read_csv(PODCASTS_DATABASE_PATH_RAW,header=None)
df_users = pd.read_csv(USER_REVIEWS_DATABASE_PATH_RAW,header=None)

In [118]:
columns_pod = ['id','name','url','studio','category','episode_count','avg_rating','total_ratings','description']
columns_users = ['id','podcasts_id','username','review_title','review','rating','date']

df_podcasts.columns = columns_pod
df_users.columns = columns_users
df_users = df_users.drop('id', axis=1)

In [119]:
df_podcasts.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2363 entries, 0 to 2362
Data columns (total 9 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   id             2363 non-null   object 
 1   name           2363 non-null   object 
 2   url            2363 non-null   object 
 3   studio         924 non-null    object 
 4   category       2363 non-null   object 
 5   episode_count  2363 non-null   int64  
 6   avg_rating     2363 non-null   float64
 7   total_ratings  2363 non-null   int64  
 8   description    2363 non-null   object 
dtypes: float64(1), int64(2), object(6)
memory usage: 166.3+ KB


In [59]:
# % of Null values
percentage_of_null_values = df_podcasts.isnull().sum()/df_podcasts.shape[0] * 100

In [60]:
df_null_distribution = pd.DataFrame(df_podcasts.isnull().sum()/df_podcasts.shape[0] * 100).reset_index()
df_null_distribution.columns = [['field in df_podcasts','% of null values']]

# Distribution of null values

In [61]:
print('Distribution of null values')
df_null_distribution.style.background_gradient()

Distribution of null values


studio column has 61% of null values and also it won't be that useful for recommendations

# Top 10 Podcasts

In [120]:
df_podcasts_top_10 = df_podcasts[df_podcasts['total_ratings'] > 70000][['name','category','episode_count','avg_rating','total_ratings']].sort_values(by=['total_ratings','avg_rating'],ascending=False).reset_index()
df_podcasts_top_10 = df_podcasts_top_10.drop('index', axis=1)


In [121]:
df_podcasts_top_10

name           category  \
0                                        Crime Junkie         True Crime   
1   My Favorite Murder with Karen Kilgariff and Ge...         True Crime   
2                                The Ben Shapiro Show               News   
3                                           The Daily               News   
4                                       Office Ladies             Comedy   
5                                  This American Life  Society & Culture   
6                                      Pardon My Take             Sports   
7                                              Morbid             Comedy   
8                                    Pod Save America               News   
9                                              Serial               News   
10               VIEWS with David Dobrik & Jason Nash             Comedy   

    episode_count  avg_rating  total_ratings  
0             282         4.8         326400  
1             683         4.6         155400  
2             350         4.4         140600  
3            1669         4.4          88100  
4             159         4.8          79900  
5              10         4.6          78300  
6             615         4.9          77600  
7             447         4.5          76000  
8             690         4.5          75100  
9              60         4.5          71100  
10            220         4.8          70500

In [84]:
df_podcasts_top_10['avg_rating'] + df_podcasts_top_10['total_ratings']

0     326404.8
1     155404.6
2     140604.4
3      88104.4
4      79904.8
5      78304.6
6      77604.9
7      76004.5
8      75104.5
9      71104.5
10     70504.8
dtype: float64

In [122]:
ll = []
for i in range(len(df_podcasts_top_10)):
    ll.append( str(df_podcasts_top_10['avg_rating'][i]) + ' ' +'(' + str(df_podcasts_top_10['total_ratings'][i]) + ')'  )
    
    
    

In [123]:
df_podcasts_top_10['combined'] = ll

In [124]:
df_podcasts_top_10

name           category  \
0                                        Crime Junkie         True Crime   
1   My Favorite Murder with Karen Kilgariff and Ge...         True Crime   
2                                The Ben Shapiro Show               News   
3                                           The Daily               News   
4                                       Office Ladies             Comedy   
5                                  This American Life  Society & Culture   
6                                      Pardon My Take             Sports   
7                                              Morbid             Comedy   
8                                    Pod Save America               News   
9                                              Serial               News   
10               VIEWS with David Dobrik & Jason Nash             Comedy   

    episode_count  avg_rating  total_ratings      combined  
0             282         4.8         326400  4.8 (326400)  
1             683         4.6         155400  4.6 (155400)  
2             350         4.4         140600  4.4 (140600)  
3            1669         4.4          88100   4.4 (88100)  
4             159         4.8          79900   4.8 (79900)  
5              10         4.6          78300   4.6 (78300)  
6             615         4.9          77600   4.9 (77600)  
7             447         4.5          76000   4.5 (76000)  
8             690         4.5          75100   4.5 (75100)  
9              60         4.5          71100   4.5 (71100)  
10            220         4.8          70500   4.8 (70500)

In [125]:
df_podcasts_top_10 = df_podcasts_top_10[['name','combined']]
df_podcasts_top_10.rename(columns={"name": "Podcast", "combined": "Ratings"},inplace=True)
df_podcasts_top_10.to_csv('Top_10_podcasts.csv',index=None)

In [126]:
ss = pd.read_csv('/Users/piyush/Desktop/dsml_Portfolio/podcast/final_push/data/processed/Top_10_podcasts.csv')

In [116]:
df_podcasts_top_10.rename(columns={"name": "Podcast", "combined": "Ratings"},inplace=True)

name      combined
0                                        Crime Junkie  4.8 (326400)
1   My Favorite Murder with Karen Kilgariff and Ge...  4.6 (155400)
2                                The Ben Shapiro Show  4.4 (140600)
3                                           The Daily   4.4 (88100)
4                                       Office Ladies   4.8 (79900)
5                                  This American Life   4.6 (78300)
6                                      Pardon My Take   4.9 (77600)
7                                              Morbid   4.5 (76000)
8                                    Pod Save America   4.5 (75100)
9                                              Serial   4.5 (71100)
10               VIEWS with David Dobrik & Jason Nash   4.8 (70500)

In [66]:
df_podcasts_top_10 = df_podcasts[df_podcasts['total_ratings'] > 70000][['name','avg_rating']].reset_index()
df_podcasts_top_10 = df_podcasts_top_10.drop('index', axis=1)

In [127]:
ss

Podcast       Ratings
0                                        Crime Junkie  4.8 (326400)
1   My Favorite Murder with Karen Kilgariff and Ge...  4.6 (155400)
2                                The Ben Shapiro Show  4.4 (140600)
3                                           The Daily   4.4 (88100)
4                                       Office Ladies   4.8 (79900)
5                                  This American Life   4.6 (78300)
6                                      Pardon My Take   4.9 (77600)
7                                              Morbid   4.5 (76000)
8                                    Pod Save America   4.5 (75100)
9                                              Serial   4.5 (71100)
10               VIEWS with David Dobrik & Jason Nash   4.8 (70500)

In [68]:
df_podcasts_top_10.columns

Index(['name', 'avg_rating'], dtype='object')

In [52]:
df = df_podcasts_top_10
fig = px.bar(df.sort_values(by='total_ratings',ascending=False), x='name', y='avg_rating',
             hover_data=['total_ratings', 'episode_count'], color='total_ratings',
             labels={'avg_rating':'average rating','name':'podcast'})
fig.update_layout(title='Top 10 Podcasts based on ratings')
fig.update_yaxes(tickfont_family="Arial Black")
fig.update_xaxes(tickfont_family="Arial Black")
fig.show()

# Top 10 podcasts with most episodes

In [14]:
import plotly.express as px
df = df_podcasts
fig = px.histogram(df, x="episode_count",nbins=20,marginal="box",
                   labels={'episode_count':'No of episodes in a podcast'})
fig.update_layout(title='Distribution of no of episodes')
fig.update_yaxes(tickfont_family="Arial Black")
fig.update_xaxes(tickfont_family="Arial Black")
fig.show()


`The distribution is highly-skewed; the median number of episodes is 140 whereas the maximum number of episodes is around 2000.`

In [15]:
df_category_avg_episode_count  = pd.DataFrame(df_podcasts.groupby(['category'])['episode_count'].mean().sort_values(ascending=False)).reset_index()
df_category_avg_episode_count.rename(columns={"episode_count": "avg_episode_count"},inplace=True)


In [16]:
df = df_category_avg_episode_count
fig = px.bar(df, x='category', y='avg_episode_count', color='avg_episode_count',
             labels={'avg_episode_count':'average episode count'})
fig.update_layout(title='Category wise average no of episodes')
fig.update_yaxes(tickfont_family="Arial Black")
fig.update_xaxes(tickfont_family="Arial Black")
fig.show()

# Distribution of top 5 categories

In [17]:
df_top_5_categories = df_podcasts[(df_podcasts['category'] == 'Business') | (df_podcasts['category'] == 'Sports') |
                (df_podcasts['category'] == 'News') | (df_podcasts['category'] == 'Science') |
                (df_podcasts['category'] == 'Leisure')]

In [18]:
import plotly.express as px
df = df_top_5_categories
fig = px.histogram(df, x="episode_count",nbins=20,marginal="box",color='category',
                   labels={'episode_count':'No of episodes in a podcast'})
fig.update_layout(title='Distribution of no of episodes for categories :: News , Sports, Science, Business, Leisure')
fig.update_yaxes(tickfont_family="Arial Black")
fig.update_xaxes(tickfont_family="Arial Black")
fig.show()


# Ratings distribution

In [19]:
df_category_avg_rating  = pd.DataFrame(df_podcasts.groupby(['category'])['avg_rating'].mean().sort_values(ascending=False)).reset_index()
df_category_avg_rating.rename(columns={"avg_rating": "avg_rating_per_category"},inplace=True)


In [20]:
df = df_category_avg_rating
fig = px.bar(df, x='category', y='avg_rating_per_category', color='avg_rating_per_category',
             labels={'avg_rating_per_category':'average rating per category'})
fig.update_layout(title='Category wise average rating')
fig.update_yaxes(tickfont_family="Arial Black")
fig.update_xaxes(tickfont_family="Arial Black")
fig.show()

In [21]:
import plotly.express as px
df = df_podcasts
fig = px.histogram(df, x="avg_rating",nbins=20,marginal="box",
                   labels={'episode_count':'No of episodes in a podcast'})
fig.update_layout(title='Distribution of average ratings')
fig.update_yaxes(tickfont_family="Arial Black")
fig.update_xaxes(tickfont_family="Arial Black")
fig.show()

In [22]:
df_top_5_categories = df_podcasts[(df_podcasts['category'] == 'Religion & Spirituality') | (df_podcasts['category'] == 'Business') |
                (df_podcasts['category'] == 'Education') | (df_podcasts['category'] == 'Comedy') |
                (df_podcasts['category'] == 'Health & Fitness')]

In [23]:
import plotly.express as px
df = df_top_5_categories
fig = px.histogram(df, x="avg_rating",nbins=20,marginal="box",color='category',
                   labels={'avg_rating':'average rating per category'})
fig.update_layout(title='Distribution of average rating for categories :: Religion & Spirituality , Business, Education, Comedy, Health & Fitness')
fig.update_yaxes(tickfont_family="Arial Black")
fig.update_xaxes(tickfont_family="Arial Black")
fig.show()


In [24]:
merged = pd.merge(df_podcasts,df_users, left_on = 'id', right_on = 'podcasts_id', how = 'inner')
merged = merged[['podcasts_id','name','url','studio','category','episode_count','avg_rating','total_ratings','description', 
       'username','review_title','review','rating','date']]
df_users_ratings = merged[['podcasts_id','name','username','category','rating']]

In [25]:

import plotly.express as px
df = df_users_ratings
fig = px.histogram(df, x="rating",nbins=10,color='rating',
                   labels={'episode_count':'No of episodes in a podcast'})
fig.update_layout(title='Distribution of ratings by users')
fig.update_yaxes(tickfont_family="Arial Black")
fig.update_xaxes(tickfont_family="Arial Black")

In [26]:
df_top_10_rated_podcasts = pd.DataFrame(df_users_ratings.groupby(by='name')['rating'].count().sort_values(ascending=False)[0:10]).reset_index()
df_top_10_rated_podcasts.rename(columns={"rating": "no of ratings per podcast"},inplace=True)

In [27]:
df_top_10_rated_podcasts

name  no of ratings per podcast
0                   Dateline NBC                       2000
1                       Culpable                       1000
2                      SmartLess                       1000
3  Rachel Maddow Presents: Ultra                       1000
4           The Ben Shapiro Show                       1000
5       Murdaugh Murders Podcast                       1000
6                   Crime Junkie                       1000
7                         Morbid                       1000
8                      The Daily                       1000
9       WorkLife with Adam Grant                        510

In [28]:
df = df_top_10_rated_podcasts
fig = px.bar(df, x='name', y='no of ratings per podcast', color='no of ratings per podcast',)
fig.update_layout(title='Top 10 Podcasts based on number of ratings')
fig.update_yaxes(tickfont_family="Arial Black")
fig.update_xaxes(tickfont_family="Arial Black")
fig.show()

In [30]:
df_podcasts.to_csv(PODCASTS_DATABASE_PATH_PROCESSED + '/' + "df_podcasts.csv")
df_users.to_csv(USER_REVIEWS_DATABASE_PATH_PROCESSED + '/' + "df_users.csv")